In [34]:
from __future__ import print_function
import argparse
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torchvision import datasets, transforms
from ax.plot.contour import plot_contour, interact_contour
from ax.plot.trace import optimization_trace_single_method
from ax.plot.diagnostic import interact_cross_validation
from ax.modelbridge.cross_validation import cross_validate
from ax.service.managed_loop import optimize
from ax.metrics.branin import branin
from ax.utils.notebook.plotting import render, init_notebook_plotting
import numpy as np
from tqdm import tqdm_notebook

init_notebook_plotting()

[INFO 09-28 15:31:35] ipy_plotting: Injecting Plotly library into cell. Do not overwrite or delete cell.


In [35]:
class Net(nn.Module):
    def __init__(self, features1, features2, kernel_size1, kernel_size2, pool1, pool2, stride1, stride2, hidden):
        super(Net, self).__init__()
        self.features1 = features1
        self.features2 = features2
        self.hidden = hidden
        self.kernel_size1 = kernel_size1
        self.kernel_size2 = kernel_size2
        self.pool1 = pool1
        self.pool2 = pool2
        self.stride1 = stride1
        self.stride2 = stride2
        
        self.conv1 = nn.Conv2d(1, self.features1, self.kernel_size1, 1)
        self.conv2 = nn.Conv2d(self.features1, self.features2, self.kernel_size2, 1)
        self.fc1 = None
        self.fc2 = nn.Linear(self.hidden, 10)

    def forward(self, x):
        x = F.relu(self.conv1(x))
        x = F.max_pool2d(x, self.pool1, self.stride1)
        x = F.relu(self.conv2(x))
        x = F.max_pool2d(x, self.pool2, self.stride2)
        if self.fc1 is None:
            self.flat_dims = x.size(1) * x.size(2) * x.size(3)
            self.fc1 = nn.Linear(self.flat_dims, self.hidden).to("cuda")
        x = x.view(-1, self.flat_dims)
        x = F.relu(self.fc1(x))
        x = self.fc2(x)
        return F.log_softmax(x, dim=1)

In [36]:
# May need to lower this depending on your GPU memory.
batch_size = 2**7
test_batch_size = 1000
num_epochs = 1
total_trials = 100
lr = 0.01
momentum = 0.5
patience= 2
use_cuda = torch.cuda.is_available()
device = torch.device("cuda" if use_cuda else "cpu")
seed = np.random.choice(10**5)
torch.manual_seed(seed)
# More workers will use more CPU. If saturating lower the value.
kwargs = {'num_workers': 8, 'pin_memory': True} if use_cuda else {}

In [37]:
train_loader = torch.utils.data.DataLoader(
    datasets.MNIST('../data', train=True, download=True,
                   transform=transforms.Compose([
                       transforms.ToTensor(),
                       transforms.Normalize((0.1307,), (0.3081,))
                   ])),
    batch_size=batch_size, shuffle=True, **kwargs)

val_loader = torch.utils.data.DataLoader(
    datasets.MNIST('../data', train=False, transform=transforms.Compose([
                       transforms.ToTensor(),
                       transforms.Normalize((0.1307,), (0.3081,))
                   ])),
    batch_size=test_batch_size, shuffle=True, **kwargs)

In [38]:
def objective(parameters):
    print(parameters)
    conv_1_out_size = parameters.get("conv_1_out_size")
    conv_2_out_size = parameters.get("conv_2_out_size")
    conv_1_kernel_size = parameters.get("conv_1_kernel_size")
    conv_2_kernel_size = parameters.get("conv_2_kernel_size")
    pool_1_kernel_size = parameters.get("pool_1_kernel_size")
    pool_2_kernel_size = parameters.get("pool_2_kernel_size")
    pool_1_stride = parameters.get("pool_1_stride")
    pool_2_stride = parameters.get("pool_2_stride")
    linear_hidden = parameters.get("linear_hidden")
    model = Net(conv_1_out_size, conv_2_out_size, conv_1_kernel_size, conv_2_kernel_size,
               pool_1_kernel_size, pool_2_kernel_size, pool_1_stride, pool_2_stride, linear_hidden).to(device)
    criterion = nn.NLLLoss()
    optimizer = optim.SGD(model.parameters(), lr=lr, momentum=momentum)

    counter = 0
    best_loss = np.inf
    for epoch in tqdm_notebook(range(num_epochs), desc="Epochs"):
        model.train()
        for i, (X_batch, y_batch) in enumerate(train_loader):
            X_batch, y_batch = X_batch.to(device), y_batch.to(device)
            if X_batch.shape[0] == 1:
                continue
            outputs = model(X_batch)
            loss = criterion(outputs, y_batch)
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            
        model.eval()
        val_loss = 0
        correct = 0
        with torch.no_grad():
            for X_batch, y_batch in val_loader:
                X_batch, y_batch = X_batch.to(device), y_batch.to(device)
                outputs = model(X_batch)
                val_loss += criterion(outputs, y_batch).item()
                pred = outputs.argmax(dim=1, keepdim=True)
                correct += pred.eq(y_batch.view_as(pred)).sum().item()
                
        # Early stopping
        val_loss /= len(val_loader.dataset)
        accuracy = correct / len(val_loader.dataset)
        if val_loss < best_loss:
            best_loss = val_loss
            counter = 0
            print("Best Accuracy: " + str(accuracy), end="\r")
        else:
            counter += 1
        if counter > patience:
            break 
    return {'nll': (best_loss, 0)}

parameters = [
    {'name': 'conv_1_out_size', 'type': 'range', 'bounds': [20, 100]},
    {'name': 'conv_2_out_size', 'type': 'range', 'bounds': [20, 100]},
    {'name': 'conv_1_kernel_size', 'type': 'range', 'bounds': [1, 5]},
    {'name': 'conv_2_kernel_size', 'type': 'range', 'bounds': [1, 5]},
    {'name': 'pool_1_kernel_size', 'type': 'range', 'bounds': [1, 5]},
    {'name': 'pool_2_kernel_size', 'type': 'range', 'bounds': [1, 5]},
    {'name': 'pool_1_stride', 'type': 'range', 'bounds': [1, 3]},
    {'name': 'pool_2_stride', 'type': 'range', 'bounds': [1, 3]},
    {'name': 'linear_hidden', 'type': 'range', 'bounds': [1, 500]},
]

In [39]:
best_parameters, values, experiment, model = optimize(
    parameters=parameters,
    experiment_name='mnist',
    objective_name='nll',
    evaluation_function=objective,
    minimize=True,
    total_trials=total_trials
)

[INFO 09-28 15:31:36] ax.service.utils.dispatch: Using Bayesian Optimization generation strategy. Iterations after 9 will take longer to generate due to model-fitting.
[INFO 09-28 15:31:36] ax.service.managed_loop: Started full optimization with 100 steps.
[INFO 09-28 15:31:36] ax.service.managed_loop: Running optimization trial 1...


{'conv_1_out_size': 58, 'conv_2_out_size': 76, 'conv_1_kernel_size': 5, 'conv_2_kernel_size': 2, 'pool_1_kernel_size': 4, 'pool_2_kernel_size': 3, 'pool_1_stride': 3, 'pool_2_stride': 3, 'linear_hidden': 141}


[INFO 09-28 15:31:41] ax.service.managed_loop: Running optimization trial 2...


{'conv_1_out_size': 34, 'conv_2_out_size': 39, 'conv_1_kernel_size': 3, 'conv_2_kernel_size': 5, 'pool_1_kernel_size': 5, 'pool_2_kernel_size': 3, 'pool_1_stride': 2, 'pool_2_stride': 2, 'linear_hidden': 374}


[INFO 09-28 15:31:46] ax.service.managed_loop: Running optimization trial 3...


...

{'conv_1_out_size': 75, 'conv_2_out_size': 31, 'conv_1_kernel_size': 4, 'conv_2_kernel_size': 5, 'pool_1_kernel_size': 5, 'pool_2_kernel_size': 3, 'pool_1_stride': 1, 'pool_2_stride': 2, 'linear_hidden': 401}


[INFO 09-28 15:55:50] ax.service.managed_loop: Running optimization trial 99...


{'conv_1_out_size': 78, 'conv_2_out_size': 33, 'conv_1_kernel_size': 4, 'conv_2_kernel_size': 5, 'pool_1_kernel_size': 4, 'pool_2_kernel_size': 3, 'pool_1_stride': 1, 'pool_2_stride': 2, 'linear_hidden': 398}


[INFO 09-28 15:56:17] ax.service.managed_loop: Running optimization trial 100...


{'conv_1_out_size': 75, 'conv_2_out_size': 31, 'conv_1_kernel_size': 4, 'conv_2_kernel_size': 5, 'pool_1_kernel_size': 5, 'pool_2_kernel_size': 3, 'pool_1_stride': 1, 'pool_2_stride': 2, 'linear_hidden': 397}


In [40]:
cv_results = cross_validate(model, folds=3)
render(interact_cross_validation(cv_results))

In [45]:
best_objectives = np.array([[trial.objective_mean for trial in experiment.trials.values()]])
best_objective_plot = optimization_trace_single_method(
    y=np.minimum.accumulate(best_objectives, axis=1),
    title="Model performance vs. # of iterations",
    ylabel="nll",
)
render(best_objective_plot)

In [42]:
best_objectives = np.array([[trial.objective_mean for trial in experiment.trials.values()]])
best_objective_plot = optimization_trace_single_method(
    y=best_objectives,
    title="Model performance at iteration",
    ylabel="nll",
)
render(best_objective_plot)

In [43]:
best_parameters

{'conv_1_out_size': 64,
 'conv_2_out_size': 20,
 'conv_1_kernel_size': 3,
 'conv_2_kernel_size': 5,
 'pool_1_kernel_size': 5,
 'pool_2_kernel_size': 3,
 'pool_1_stride': 1,
 'pool_2_stride': 2,
 'linear_hidden': 406}

In [44]:
%matplotlib inline
render(interact_contour(model=model, metric_name='nll'))